In [1]:
import pandas as pd
from io import StringIO
import requests
import spacy

url = "https://docs.google.com/spreadsheets/d/e/2PACX-1vTSLyp3Ev2bxe8pnHStFtbdwg-EhvbMEhEUzRsaFjC0sKVQ-OzyD8LbAjM9iYoG2LSmSTAGGFfed4I9/pub?gid=0&single=true&output=csv"

df=pd.read_csv(StringIO(requests.get(url).content.decode('utf-8')))
display(df.head())

spacyNLP = spacy.load('de')

Level                    Title  \
0    A1            Meine Familie   
1    A1   Maria und ihre Familie   
2    A1              Ich bin Tom   
3    A1              Freundinnen   
4    A1  Einkaufen im Supermarkt   

                                                Text  \
0  Zu meiner Familie gehören vier Personen. Die M...   
1  Mein Name ist Maria. Ich bin 30 Jahre alt. Zu ...   
2  Hallo! Ich bin Tom Maier. Ich bin 13 Jahre alt...   
3  Ricarda ist 21 Jahre alt und wohnt in Lübeck. ...   
4  Frau Meier geht heute in den Supermarkt. Ihr M...   

                                       Source     Type  
0         https://german.net/reading/familie/  Reading  
1  https://german.net/reading/marias-familie/  Reading  
2             https://german.net/reading/tom/  Reading  
3     https://german.net/reading/freundinnen/  Reading  
4       https://german.net/reading/einkaufen/  Reading

In [2]:
#clean data
import re

import string
import spacy
import hunspell
spellchecker = hunspell.HunSpell('/usr/share/hunspell/de_DE.dic',
                                 '/usr/share/hunspell/de_DE.aff')

correct = [",", "!", "?" , "\"", ":", "/", "*", "(", ")", "%", "-", ";"
           "Valerie", "Lena", "Lana", "Micki", "Maier", "Ricarda", "Maike", "Struppi", "Mayer", "Leonie", "Valerie", "Müritzsee",
          'Disko', 'Nikolaustag', 'Jana', 'blitzeblank', 'Urenkelkinder',]
for word in correct:
    spellchecker.add(word)

def isUmlautError(string, corrected):
    matches = difflib.SequenceMatcher(None, corrected, string).get_matching_blocks()
    rest = corrected
    for match in reversed(matches):
        rest[match.a:match.a + match.size] = []

    return set(rest)<set('äöüÄÖÜ')

def isCapitalisationError(string, corrected):
    return (string[1:] == corrected[1:] and string[0].lower() == corrected[0].lower())


def spellcheck(text):
    total=0
    numberSpellingErrorsWithCorrection=0
    numberSpellingErrorsWithoutCorrection=0
    numberUmlautSpellingErrors=0
    numberCapitalisationErrors=0
    
    correctedText = text
    for word in reversed(list(spacyNLP(text))):
        if not spellchecker.spell(word.text): # and word not in exclude:
            total+=1
            try:
                suggestions = spellchecker.suggest(word.text)
                autocorrected = suggestions[0]
                index = word.idx
                length = len(word.text)
                print(str(word.text + " --> " + autocorrected))
                correctedText = correctedText[:index] + autocorrected + correctedText[index + length:]
                if isUmlautError(word.text, correctedText):
                    numberUmlautSpellingErrors+=1
                elif isCapitalisationError(string, corrected):
                    numberCapitalisationErrors+=1
                numberSpellingErrorsWithCorrection+=1
            except IndexError:
                numberSpellingErrorsWithoutCorrection+=1
                print(str(word.text + " --> "))
    
    ratioSpellingErrorsWithCorrection = numberSpellingErrorsWithCorrection/total
    ratioSpellingErrorsWithoutCorrection = numberSpellingErrorsWithoutCorrection/total
    ratioSpellingErrors = (numberSpellingErrorsWithoutCorrection + numberSpellingErrorsWithCorrection)/total
    ratioUmlautSpellingErrors=numberUmlautSpellingErrors/total
    ratioCapitalisationErrors=numberCapitalisationErrors/total
    ratioRealSpellingErrors=(numberSpellingErrorsWithoutCorrection + numberSpellingErrorsWithCorrection - numberUmlautSpellingErrors - numberCapitalisationErrors) / total 
            
    return correctedText, totalWords, ratioRealSpellingErrors, ratioSpellingErrors, ratioSpellingErrorsWithCorrection, ratioSpellingErrorsWithoutCorrection,ratioUmlautSpellingErrors, ratioCapitalisationErrors

def clean(text):
    text, totalWords, ratioSpellingErrors, ratioSpellingErrorsWithCorrection, ratioSpellingErrorsWithoutCorrection,ratioUmlautSpellingErrors, ratioCapitalisationErrors = spellcheck(text)
    text = re.sub("Stadt X\,?\.?\s?(den )?\d+((\,)|(\.)|(\-))\d+((\,)|(\.)|(\. )|(\-))\d+ ", "", text)
    text = re.sub("^.{10,250}Sehr gee?h?e?e?rte?( Damen )?((und)|(oder))? He?er?ren", "Sehr geehrte Damen und Herren", text)
    text = re.sub("^.{10,100}Sehr Geherte mein Damen und Herren", "Sehr geehrte Damen und Herren", text)
    text = re.sub("^.{10,100}Liebe Dana", "Liebe Dana", text)
    text = re.sub("^.{10,100}Lieber? Silke", "Liebe Silke", text)
    text = re.sub("^.{10,100}Liebe Maria", "Liebe Maria", text)
    text = re.sub("^.{10,100}Liebe Katharina", "Liebe Katharina", text)
    text = re.sub("(\S+)\.(\S+)", r"\1. \2", text)
    text = re.sub("www. ", r"www.", text)
    text = re.sub("^.{10,100}Lieber Michael", "Lieber Michael", text)
    text = re.sub("^.{10,100}Lieber Ingo", "Lieber Ingo", text)
    text = re.sub("^.{10,100}Lieber Julia", "Lieber Julia", text)
    text = re.sub("^.{10,100}Lieber Eva", "Lieber Eva", text)
    text = re.sub("^.{10,100}Hallo Eva", "Hallo Eva", text)
    text = re.sub("^.{10,100}Liebe Julia", "Liebe Julia", text)
    text = re.sub("^.{10,100}Hallo Julia", "Hallo Julia", text)
    text = re.sub("^.{10,200}Sehr geerhte Damen und Herren", "Sehr geehrte Damen und Herren", text)
    text = re.sub("^.{10,200}Sehr Geehrte Damen und Herren", "Sehr geehrte Damen und Herren", text)
    text = re.sub("^.{10,200}Sehr geehrte Damen und Herrn", "Sehr geehrte Damen und Herren", text)
    text = re.sub("^.{10,200}See?hr gerrhte Herren und Damen", "Sehr geehrte Damen und Herren", text)
    text = re.sub("^.{10,200}Sehr geehte Damen und Herr", "Sehr geehrte Damen und Herren", text)
    text = re.sub("^.{10,200}Seehr geehrte Damen und Herren", "Sehr geehrte Damen und Herren", text)
    text = re.sub("^.{10,200}Seher geherte Damen und Herren", "Sehr geehrte Damen und Herren", text)
    text = re.sub("^.{10,200}Sehr geherte Herrn", "Sehr geehrte Herren", text)
    text = re.sub("^.{10,200}Sehr geehrte Fir", "Sehr geehrte Fir", text)
    text = re.sub("^.{10,200}Sehr geehrte Damen u. Herren", "Sehr geehrte Damen und Herren", text)
    text = re.sub("^.{10,200}Sehr geehrte Damen u Herren", "Sehr geehrte Damen und Herren", text)
    text = re.sub("^.{10,200}Seehr Geehrte Damen und He", "Sehr geehrte Damen und He", text)
    text = re.sub("^.{10,200}Sehr geehrte Au-", "Sehr geehrte Au-", text)
    text = re.sub("^.{10,200}SEHR GEEHRTE DAMEN UND HERREN", "Sehr geehrte Damen und Herren", text)
    
    return text, ratioSpellingErrors, ratioSpellingErrorsWithCorrection, ratioSpellingErrorsWithoutCorrection,ratioUmlautSpellingErrors, ratioCapitalisationErrors
    


In [3]:
df.head()

Level                    Title  \
0    A1            Meine Familie   
1    A1   Maria und ihre Familie   
2    A1              Ich bin Tom   
3    A1              Freundinnen   
4    A1  Einkaufen im Supermarkt   

                                                Text  \
0  Zu meiner Familie gehören vier Personen. Die M...   
1  Mein Name ist Maria. Ich bin 30 Jahre alt. Zu ...   
2  Hallo! Ich bin Tom Maier. Ich bin 13 Jahre alt...   
3  Ricarda ist 21 Jahre alt und wohnt in Lübeck. ...   
4  Frau Meier geht heute in den Supermarkt. Ihr M...   

                                       Source     Type  
0         https://german.net/reading/familie/  Reading  
1  https://german.net/reading/marias-familie/  Reading  
2             https://german.net/reading/tom/  Reading  
3     https://german.net/reading/freundinnen/  Reading  
4       https://german.net/reading/einkaufen/  Reading

In [4]:
def setupRFTagger():
    import urllib
    url = "http://www.cis.uni-muenchen.de/~schmid/tools/RFTagger/data/RFTagger.tar.gz"
    filename = "RFTagger.tar.gz"
    urllib.request.urlretrieve(url, filename)
    import tarfile
    tar = tarfile.open(filename)
    tar.extractall()
    tar.close()
    from subprocess import run
    run(["make"], cwd="RFTagger/src")
    
def setupParser():
    #!pip install standordcorenlp
    #!apt install openjdk-11-jre

    #download Stanford Parser
    import urllib
    url = "http://nlp.stanford.edu/software/stanford-corenlp-full-2018-02-27.zip"
    filename = "stanford-corenlp-full-2018-02-27.zip"
    urllib.request.urlretrieve(url, filename)
    import zipfile
    zip_obj = zipfile.ZipFile(filename)
    zip_obj.extractall()
    zip_obj.close()

    url = "http://nlp.stanford.edu/software/stanford-german-corenlp-2018-02-27-models.jar"
    filename = "stanford-german-corenlp-2018-02-27-models.jar"
    urllib.request.urlretrieve(url, filename)

    import shutil
    shutil.move("./stanford-german-corenlp-2018-02-27-models.jar", "./stanford-corenlp-full-2018-02-27/stanford-german-corenlp-2018-02-27-models.jar")

In [5]:
from subprocess import check_output
from tqdm import tqdm
import threading

#stanford parser

from stanfordcorenlp import StanfordCoreNLP
import re
import sys

    
def sentenceParsing(sentence, nlp):
    try:
        tree = re.sub(" +", " ", nlp.parse(sentence.text).replace("\n", ""))
        return tree
    except ValueError:
        return ""
        
    return output

def sentenceTagging(sentence):
    print(sentence)
    tempFile = open("RFTagger/temp.txt", "w")
    tempFile.write("\n".join([word.text for word in sentence]))
    tempFile.close()
    sentence_tagged = check_output(["src/rft-annotate", "lib/german.par", "temp.txt"], cwd="RFTagger").decode("utf-8").split("\n")
    sentence_tagged_saparated= []
    for entry in sentence_tagged:
        temp = entry.split("\t")
        if len(temp) == 2:
            sentence_tagged_saparated.append([temp[0]] + temp[1].split("."))
        elif len(temp) == 1 and temp[0] == '':
            continue
                
    return sentence_tagged_saparated

def preprocessing(df):
    df["newLevel"] = [element[0] for element in df["Level"]]
    df["cleanedText"], df["ratioSpellingErrors"], df["ratioSpellingErrorsWithCorrection", df["ratioSpellingErrorsWithoutCorrection" ,df["ratioUmlautSpellingErrors"], df["ratioCapitalisationErrors"] = [clean(text) for text in tqdm(df["Text"])]
    
    taggedTexts = []
    taggedSentences = []
    
    pasedTexts = []
    parsedSentences = []
    
    sentences = []
    sentenceLevels = []
    
    
    nlp = StanfordCoreNLP(r'./stanford-corenlp-full-2018-02-27', lang='de', memory='2g')
    
    for index, row in tqdm(df.iterrows()):
        doc = spacyNLP(row["cleanedText"])
        newTaggedText =[]
        newParsedText = []
        for sentence in list(doc.sents):
            newTaggedSentence = sentenceTagging(sentence)
            newTaggedText.append(newTaggedSentence)
            taggedSentences.append(newTaggedSentence)

            newParsedSentence = sentenceParsing(sentence, nlp)
            newParsedText.append(newParsedSentence)
            parsedSentences.append(newParsedSentence)

            sentences.append(sentence.text)
            sentenceLevels.append(row["newLevel"])

        taggedTexts.append(newTaggedText)
        pasedTexts.append(newParsedText)
    
    nlp.close()  # Do not forget to close! The backend server will consume a lot memory.
    
    df["RFTagger"] = taggedTexts
    df["parsedText"] = pasedTexts
    
    sentence_df = pd.DataFrame()
    sentence_df["Text"] = sentences
    sentence_df["newLevel"] = sentenceLevels
    sentence_df["taggedSentences"] = taggedSentences
    sentence_df["parsedSentences"] = parsedSentences
    
    return df, sentence_df

In [6]:
df, sentence_df = preprocessing(df)

  0%|          | 5/1834 [00:00<02:15, 13.54it/s]

Königstraße --> Königstrasse
1234/567890 --> 
Ricardas --> Ricarda


  1%|          | 10/1834 [00:00<01:46, 17.17it/s]

Mimi --> Mini
Mimi --> Mini
Teck --> Eck


  1%|          | 12/1834 [00:01<03:50,  7.90it/s]

...

1832it [7:02:03, 13.82s/it]

Zusammenfassung:
Pragmatische Wettbewerbsorientiert
Maibauer beschäftigt sich in dem vorliegenden Auszug aus seinem Buch "
Pragmatik.
Eine Einführung" mit zwei pragmatischen Prinzipien, die für den Spracherwerb von Bedeutung seien.
Maibauer geht vom Erstspracherwerb bei Kleinkindern aus, merkt aber an, dass die Ergebnisse auch auf die Pragmatik erwachsener Sprecher bzw. Sprachlernerz anzuwenden seien.
Einleitend weist Maibauer daraufhin, dass Kinder zwischen dem zweiten und sechsten Lebensjahr eine grobe Zahl neuer Wärter in ihren Wortschatz aufnehmen.
Die besondere Schwierigkeit beim Erwerb des Wortschatzes liegt darin,neue Wärter aus der Masse an Einput herauszufiltern, diese zu speichern und mit Eigenschaften zu versehen, damit sie adäquat verwendet werden kennen.
Laut Klarlack sind in diesem Prozess 2 Prinzipien entscheidend: das Prinzip der Konventionalstrafe und das Prinzip des Kontrasts.
Ersteres besagt, dass für jede Bedeutung eine Form existiert, das heilt jedem Wort
ist eine 

1833it [7:02:19, 13.82s/it]

Zusammenfassen
Kapitel "
6
. 6 Textgrenzen" des Studienbuches Linguistik (Linke, Nussbaum, Postmann, Tübingen 1994 2, S. 255/256) behandelt die Problematik der Definition von Textgrenzen.
Der Begriff "Text" ist bei eingehen derer Untersuchung nicht eindeutig, da es sprachliche gerungen gibt, bei denen die Textgrenzen diffus zu sein scheinen.
So sind bspw. Kochrezepte in ihren Grenzen klar definiert, Gespräche hingegen weniger klar.
Mit mehreren Kriterien, die jeweils problematisiert werden, erörtern die Autoren die Frage nach den T. - Grenzen.
Mit der kommunikativen Funktion lassen sich sehr kleine (kurze) Sprachunabhängigen als Text erfassen, allerdings wird nach Sinnhaftigkeit dieses Kriteriums gefragt (ohne den -unsinn derselben weiter auszufahren).
So erde das Kriterium mehrerer Sitze (aber was ist ein Satz?), die Kohärenz aufweisen, dem Alltagsverständnis mehr entsprechen (Doch was wer damit gewonnen?).
Bei dem Problem von sprach.
Produkten, die sehr! umfangreich sind und deshalb 

1834it [7:02:37, 13.83s/it]


In [7]:
df.head()

Level                    Title  \
0    A1            Meine Familie   
1    A1   Maria und ihre Familie   
2    A1              Ich bin Tom   
3    A1              Freundinnen   
4    A1  Einkaufen im Supermarkt   

                                                Text  \
0  Zu meiner Familie gehören vier Personen. Die M...   
1  Mein Name ist Maria. Ich bin 30 Jahre alt. Zu ...   
2  Hallo! Ich bin Tom Maier. Ich bin 13 Jahre alt...   
3  Ricarda ist 21 Jahre alt und wohnt in Lübeck. ...   
4  Frau Meier geht heute in den Supermarkt. Ihr M...   

                                       Source     Type newLevel  \
0         https://german.net/reading/familie/  Reading        A   
1  https://german.net/reading/marias-familie/  Reading        A   
2             https://german.net/reading/tom/  Reading        A   
3     https://german.net/reading/freundinnen/  Reading        A   
4       https://german.net/reading/einkaufen/  Reading        A   

                                         cleanedText  \
0  Zu meiner Familie gehören vier Personen. Die M...   
1  Mein Name ist Maria. Ich bin 30 Jahre alt. Zu ...   
2  Hallo! Ich bin Tom Maier. Ich bin 13 Jahre alt...   
3  Ricarda ist 21 Jahre alt und wohnt in Lübeck. ...   
4  Frau Meier geht heute in den Supermarkt. Ihr M...   

                                            RFTagger  \
0  [[[Zu, APPR, Dat], [meiner, PRO, Poss, Attr, -...   
1  [[[Mein, PRO, Poss, Attr, -, Nom, Sg, Masc], [...   
2  [[[Hallo, ITJ], [!, SYM, Pun, Sent]], [[Ich, P...   
3  [[[Ricarda, N, Name, Nom, Sg, Fem], [ist, VFIN...   
4  [[[Frau, N, Reg, Nom, Sg, Fem], [Meier, N, Nam...   

                                          parsedText  
0  [(ROOT (S (PP (APPR Zu) (PPOSAT meiner) (NN Fa...  
1  [(ROOT (S (NP (PPOSAT Mein) (NN Name)) (VAFIN ...  
2  [(ROOT (NUR (ITJ Hallo) ($. !))), (ROOT (S (PP...  
3  [(ROOT (CS (S (NE Ricarda) (VAFIN ist) (AP (NP...  
4  [(ROOT (S (NP (NN Frau) (NE Meier)) (VVFIN geh...

In [8]:
sentence_df.head()

Text newLevel  \
0           Zu meiner Familie gehören vier Personen.        A   
1  Die Mutter bin ich und dann gehört natürlich m...        A   
2  Wir haben zwei Kinder, einen Sohn, der sechs J...        A   
3  Wir wohnen in einem kleinen Haus mit einem Gar...        A   
4       Dort können die Kinder ein bisschen spielen.        A   

                                     taggedSentences  \
0  [[Zu, APPR, Dat], [meiner, PRO, Poss, Attr, -,...   
1  [[Die, ART, Def, Nom, Sg, Fem], [Mutter, N, Re...   
2  [[Wir, PRO, Pers, Subst, 1, Nom, Pl, *], [habe...   
3  [[Wir, PRO, Pers, Subst, 1, Nom, Pl, *], [wohn...   
4  [[Dort, ADV], [können, VFIN, Mod, 3, Pl, Pres,...   

                                     parsedSentences  
0  (ROOT (S (PP (APPR Zu) (PPOSAT meiner) (NN Fam...  
1  (ROOT (CS (S (NP (ART Die) (NN Mutter)) (VAFIN...  
2  (ROOT (S (PPER Wir) (VAFIN haben) (CNP (NP (CA...  
3  (ROOT (S (PPER Wir) (VVFIN wohnen) (PP (APPR i...  
4  (ROOT (S (ADV Dort) (VMFIN können) (NP (ART di...

In [ ]:

def executer(df, function, part_of_df, new_column):
    result = []
    for entry in tqdm(df[part_of_df]):
        
        result.append(function(entry))

    df[new_column]=result

In [ ]:
#df["newLevel"] = [element[0] for element in df["Level"]]
#df["cleanedText"] = [clean(text) for text in tqdm(df["Text"])]
#df["RFTagger"] = [preprocessing(text) for text in tqdm(df["cleanedText"])]
#nlp = StanfordCoreNLP(r'./stanford-corenlp-full-2018-02-27', lang='de', memory='2g')
#df["parsedText"] = [parsing(text) for text in tqdm(df["cleanedText"])]
#nlp.close()  # Do not forget to close! The backend server will consume a lot memory.


In [9]:
def save_df(path,df):
    df.to_csv(path,sep="|",index=False)
    
display(df.head())
filename = "01_Preprocessing_df.csv"
save_df(filename, df)

display(sentence_df.head(n=100))
filename = "01a_Sentence_df.csv"
save_df(filename, sentence_df)

Level                    Title  \
0    A1            Meine Familie   
1    A1   Maria und ihre Familie   
2    A1              Ich bin Tom   
3    A1              Freundinnen   
4    A1  Einkaufen im Supermarkt   

                                                Text  \
0  Zu meiner Familie gehören vier Personen. Die M...   
1  Mein Name ist Maria. Ich bin 30 Jahre alt. Zu ...   
2  Hallo! Ich bin Tom Maier. Ich bin 13 Jahre alt...   
3  Ricarda ist 21 Jahre alt und wohnt in Lübeck. ...   
4  Frau Meier geht heute in den Supermarkt. Ihr M...   

                                       Source     Type newLevel  \
0         https://german.net/reading/familie/  Reading        A   
1  https://german.net/reading/marias-familie/  Reading        A   
2             https://german.net/reading/tom/  Reading        A   
3     https://german.net/reading/freundinnen/  Reading        A   
4       https://german.net/reading/einkaufen/  Reading        A   

                                         cleanedText  \
0  Zu meiner Familie gehören vier Personen. Die M...   
1  Mein Name ist Maria. Ich bin 30 Jahre alt. Zu ...   
2  Hallo! Ich bin Tom Maier. Ich bin 13 Jahre alt...   
3  Ricarda ist 21 Jahre alt und wohnt in Lübeck. ...   
4  Frau Meier geht heute in den Supermarkt. Ihr M...   

                                            RFTagger  \
0  [[[Zu, APPR, Dat], [meiner, PRO, Poss, Attr, -...   
1  [[[Mein, PRO, Poss, Attr, -, Nom, Sg, Masc], [...   
2  [[[Hallo, ITJ], [!, SYM, Pun, Sent]], [[Ich, P...   
3  [[[Ricarda, N, Name, Nom, Sg, Fem], [ist, VFIN...   
4  [[[Frau, N, Reg, Nom, Sg, Fem], [Meier, N, Nam...   

                                          parsedText  
0  [(ROOT (S (PP (APPR Zu) (PPOSAT meiner) (NN Fa...  
1  [(ROOT (S (NP (PPOSAT Mein) (NN Name)) (VAFIN ...  
2  [(ROOT (NUR (ITJ Hallo) ($. !))), (ROOT (S (PP...  
3  [(ROOT (CS (S (NE Ricarda) (VAFIN ist) (AP (NP...  
4  [(ROOT (S (NP (NN Frau) (NE Meier)) (VVFIN geh...

Text newLevel  \
0            Zu meiner Familie gehören vier Personen.        A   
1   Die Mutter bin ich und dann gehört natürlich m...        A   
2   Wir haben zwei Kinder, einen Sohn, der sechs J...        A   
3   Wir wohnen in einem kleinen Haus mit einem Gar...        A   
4        Dort können die Kinder ein bisschen spielen.        A   
5   Unser Sohn kommt bald in die Schule, unsere To...        A   
6           Meine Kinder sind am Nachmittag zu Hause.        A   
7                        So arbeite ich nur halbtags.        A   
8   Eigentlich gehören zu unserer Familie auch noc...        A   
9                           Sie wohnen nicht bei uns.        A   
10                    Sie haben ein Haus in der Nähe.        A   
11                 Die Kinder gehen sie oft besuchen.        A   
12                               Mein Name ist Maria.        A   
13                              Ich bin 30 Jahre alt.        A   
14  Zu meiner Familie gehören außer mir noch drei ...        A   
15                 Mein Mann Markus ist 31 Jahre alt.        A   
16                             Wir haben zwei Kinder.        A   
17            Unser Sohn Heinrich ist drei Jahre alt.        A   
18           Unsere Tochter Valerie ist ein Jahr alt.        A   
19         Wir haben auch einen Hund und zwei Katzen.        A   
20  Der Hund heißt Maya und die Katzen Lana und Mi...        A   
21                          Wir wohnen in einem Dorf.        A   
22         Die Stadt ist nicht weit von uns entfernt.        A   
23         Unser Haus ist klein und hat einen Garten.        A   
24                     Dort spielen die Kinder gerne.        A   
25  Heinrich geht in den Kindergarten, und Valerie...        A   
26  Meine Eltern leben im Ausland, aber die Eltern...        A   
27       Ich gehe sie mit den Kindern gerne besuchen.        A   
28            Oft passen sie auch auf die Kinder auf.        A   
29  Ich bin Journalistin und arbeite meistens von ...        A   
..                                                ...      ...   
70        Danach trinken wir Kaffee und essen Kuchen.        A   
71  Im Café neben dem Supermarkt gibt es sehr gute...        A   
72                                      Frau Meier: "        A   
73                                       Gute Idee!".        A   
74  Frau Meier und Frau Schmidt gehen zusammen in ...        A   
75                                      Frau Meier: "        A   
76                               Ich brauche Tomaten.        A   
77                        Mein Mann will Salat essen.        A   
78                          Ich nehme zehn Tomaten. "        A   
79                                    Frau Schmidt: "        A   
80                                  Tomaten sind gut.        A   
81                            Ich kaufe fünf Tomaten.        A   
82                           Da ist auch Kopfsalat. "        A   
83                 Frau Meier nimmt keinen Kopfsalat.        A   
84                        Sie nimmt aber zwei Gurken.        A   
85           Frau Meier kauft auch ein Kilo Zwiebeln.        A   
86                     Frau Schmidt will Brot kaufen.        A   
87                                      Frau Meier: "        A   
88                          Das Brot ist nicht schön.        A   
89                    Ich kaufe Brot in der Bäckerei.        A   
90                  Aber die Schokolade hier ist gut.        A   
91                            Sie kostet nur 50 Cent.        A   
92                Ich nehme drei Tafeln Schokolade. "        A   
93                                    Frau Schmidt: "        A   
94                     Da ist noch ein Sonderangebot.        A   
95       Mineralwasser und Orangensaft sind billig. "        A   
96                                      Frau Meier: "        A   
97                     Orangensaft habe ich zu Hause.        A   
98    Aber ich brauche fünf Flaschen Mineralwasser. "        A   
99  Frau Schmidt kauft 

In [ ]:
###Create Sentence Dataset###
levelsText = []
sentences = []
for text, level in tqdm(zip(df["cleanedText"], df["Level"])):
    for sentence in sent_tokenize(text):
        levelsText.append(level)
        sentences.append(sentence)

sentence_df= pd.DataFrame()
sentence_df["Text"] = sentences
sentence_df["Level"] = levelsText
df["newLevel"] = levelsText[0]
executer(sentence_df, preprocessing, "Text", "RFTagger")
nlp = StanfordCoreNLP(r'./stanford-corenlp-full-2018-02-27', lang='de', memory='2g')
executer(sentence_df, parsing, "Text", "parsedText")
nlp.close()  # Do not forget to close! The backend server will consume a lot memory.

sentence_df.head()



In [ ]:
display(sentence_df.head(n=100))
filename = "01a_Sentence_df.csv"
save_df(filename, sentence_df)

In [ ]:
for number in range(1, 2):
    text = df.loc[number , "cleanedText"]
    print(preprocessing(text))

In [ ]:

sentenceTagging(spacyNLP("Mama beruhigt Papa und meint , dass das Geschenk bereits im Festsaal ist , wo alle eingeladenen Gäste warten ."))